![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 12. <i>Key logging</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Badania nad komputerowym wspomaganiem tłumaczenia często prowadzone są przy użyciu metodologii testowania interfejsów użytkownika - UI/UX testing. Program typu CAT traktuje się wówczas jak każdy inny program komputerowy i przeprowadza testy wydajności i użyteczności.

Testy takie prowadzone są zawsze na użytkownikach końcowych, w tym przypadku - na tłumaczach. Podstawowym celem testów jest próba zaobserwowania faktycznego sposobu pracy tłumacza - które funkcje programu są przez niego wykorzystywane najczęściej, jakich innych narzędzi poza CAT-em używa on do swojej pracy, które funkcje programu działają zgodnie, a które niezgodnie z intuicją użytkownika oraz wiele innych czynników. Aby wszystkie te analizy były możliwe, konieczne jest zgromadzenie jak największej ilości danych dotyczących przebiegu testu.

Testy są przede wszystkim nagrywane. Nagrywany jest zarówno ekran komputera (screen capture), jak i sam użytkownik pracujący przy komputerze. To jednak nie wszystko - często stosuje się specjalne techniki eye-trackingu, które są w stanie określić, w który punk ekranu użytkownik aktualnie patrzy. Dane pozyskane w ten sposób używane są do analizy czasu znalezienia przez użytkownika potrzebnej mu funkcji oraz zidentyfikowania miejsc, gdzie tej funkcji poszukiwał. Można również wyznaczyć obszary ekranu, które często skupiają uwagę użytkownika. 

Dodatkowo stosuje się jeszcze jedną technikę, która jest szczególnie przydatna z punktu widzenia analizy procesu tłumaczenia. Wykonuje się pełny key logging, tj. zapisuje się każde uderzenie użytkownika w dowolny klawisz na klawiaturze wraz z precyzyjnym czasem tego uderzenia. Dane pozyskane w ten sposób pozwalają na przeprowadzenie szeregu interesujących analiz.

Zapoznajmy się najpierw z programem typu key logger:

`sudo pip3 install keyboard`

In [6]:
import keyboard
from datetime import datetime

def log_key(key):
    with open("txt/keylog.txt", "a") as f:
        f.write(f"{datetime.now()} - {key.name}\n")

keyboard.on_press(log_key)

keyboard.wait()


KeyboardInterrupt: 

UWAGA! Aby uruchomić powyższy kod na Linuxie konieczne są uprawnienia administratora (pytanie poza konkursem - dlaczego?)

### Ćwiczenie 1: Wykorzystując powyższy kod napisz keylogger, który zapisuje wszystkie uderzenia w klawisze do pliku. Format pliku jest dowolny, każdy wpis musi zawierać precyzyjną godzinę uderzenia oraz uderzony klawisz. Uruchom program i przepisz paragraf dowolnie wybranego tekstu.

In [5]:
import keyboard
import time

def log_keystroke(event):
    with open("txt/keystroke_log.txt", "a") as log_file:
        log_time = time.strftime("%Y-%m-%d %H:%M:%S", time.localtime())
        log_file.write(f"{log_time} - {event.name}\n")

keyboard.on_press(log_keystroke)
keyboard.wait()

<function keyboard.hook.<locals>.remove_()>

Celem powyższego ćwiczenia jest pozyskanie danych testowych. Dalsze analizy będziemy prowadzili już bez key loggera, starając się korzystać jedynie z danych zapisanych w pliku. Oczywiście, jeśli zajdzie taka konieczność, można w każdej chwili wygenerować sobie nowy plik.

### Ćwiczenie 2: Napisz program, który wyliczy średnią prędkość pisania. Wykryj, kiedy użytkownik zaczął pisać. Nie bierz pod uwagę przerw dłuższych niż 5 sekund. Podaj prędkość pisania w znakach na minutę oraz słowach na minutę.

In [1]:
from pynput import keyboard
from datetime import datetime, timedelta

key_times = []
last_time = None

def on_press(key):
    global last_time
    current_time = datetime.now()
    
    if last_time and (current_time - last_time) > timedelta(seconds=5):
        key_times.clear()
    
    key_times.append(current_time)
    last_time = current_time

def calculate_speed():
    if len(key_times) < 2:
        print("Zbyt mało danych do obliczenia prędkości pisania.")
        return
    
    total_time = (key_times[-1] - key_times[0]).total_seconds() / 60
    
    num_chars = len(key_times)
    num_words = num_chars / 5
    
    chars_per_minute = num_chars / total_time
    words_per_minute = num_words / total_time
    
    print(f"Średnia prędkość pisania: {chars_per_minute:.2f} znaków na minutę")
    print(f"Średnia prędkość pisania: {words_per_minute:.2f} słów na minutę")

def on_release(key):
    if key == keyboard.Key.esc:
        calculate_speed()
        return False

with keyboard.Listener(on_press=on_press, on_release=on_release) as listener:
    print("Rozpocznij pisanie. Naciśnij 'esc' aby zakończyć i zobaczyć wyniki.")
    listener.join()



This process is not trusted! Input event monitoring will not be possible until it is added to accessibility clients.


Rozpocznij pisanie. Naciśnij 'esc' aby zakończyć i zobaczyć wyniki.
Średnia prędkość pisania: 733.09 znaków na minutę
Średnia prędkość pisania: 146.62 słów na minutę


Wróćmy teraz do procesu tłumaczenia. Analiza uderzeń klawiszy wykonanych podczas tłumaczenia pozwala wykryć dłuższe pauzy. Pauzy te najczęściej wskazują miejsca, w których tłumacz musi się głębiej zastanowić nad tłumaczeniem danego słowa lub frazy. Przerwę tę wykorzystuje na przykład na sprawdzenie tłumaczenia lub definicji w słowniku, przeglądanie wyników z pamięci tłumaczeń lub korzystanie z innych pomocy (eye-tracking mógłby w tym przypadku rozstrzygnąć, czym w istocie zajmuje się w tym momencie tłuamcz). Jest też możliwe, że tłumacz poświęca pauzę na tzw. cognitive pause-and-unload - rodzaj zamyślenia, pozwalający oczyścić myśli. Z punktu widzenia projektowania systemu wspomagającego tłumaczenie niezwykle istotna jest informacja, nad czym tłumacz musi się dłużej zastanowić. Minimalizacja liczby i czasu trwania takich przerw jest szansą na usprawnienie procesu tłumaczenia.

### Ćwiczenie 3: Napisz program do wykrywania przerw w pisaniu. Raportuj długość oraz miejsce wystąpienia przerwy podając 20-znakowy kontekst z każdej strony. Wykryj każdą przerwę dłuższą niż 3 sekundy, posortuj wyniki malejąco po długości przerwy.

In [7]:
from pynput import keyboard
from datetime import datetime, timedelta

key_times = []
key_text = []
last_time = None
breaks = []

def key_to_string(key):
    try:
        return key.char
    except AttributeError:
        if key == keyboard.Key.space:
            return ' '
        return f'[{str(key)}]'

def on_press(key):
    global last_time
    current_time = datetime.now()
    
    key_times.append(current_time)
    key_text.append(key_to_string(key))
    
    if last_time and (current_time - last_time) > timedelta(seconds=3):
        context_start = max(0, len(key_text) - 20)
        context_end = len(key_text)
        context_before = ''.join(key_text[context_start:context_end])
        
        context_start = len(key_text)
        context_end = min(len(key_text) + 20, len(key_text))
        context_after = ''.join(key_text[context_start:context_end])
        
        breaks.append((current_time - last_time, context_before, context_after))
    
    last_time = current_time

def report_breaks():
    if not breaks:
        print("Nie wykryto przerw dłuższych niż 3 sekundy.")
        return
    
    breaks.sort(reverse=True, key=lambda x: x[0])
    
    for duration, context_before, context_after in breaks:
        print(f"Przerwa: {duration.total_seconds():.2f} sekund")
        print(f"Kontekst przed przerwą: ...{context_before}")
        print(f"Kontekst po przerwie: {context_after}...")
        print()

def on_release(key):
    if key == keyboard.Key.esc:
        report_breaks()
        return False

with keyboard.Listener(on_press=on_press, on_release=on_release) as listener:
    print("Rozpocznij pisanie. Naciśnij 'esc' aby zakończyć i zobaczyć wyniki.")
    listener.join()



This process is not trusted! Input event monitoring will not be possible until it is added to accessibility clients.


Rozpocznij pisanie. Naciśnij 'esc' aby zakończyć i zobaczyć wyniki.
Przerwa: 3.82 sekund
Kontekst przed przerwą: ...fsdjfdnsjfjdnfjdfnj[Key.esc]
Kontekst po przerwie: ...

